In [1]:
!pip install autogluon

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.0/44.0 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 2.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 2.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 259.5/259.5 kB 9.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
INFO: pip is looking at multiple versions of openxlab to determine which version is compatible with other requirements. This could take a while.
INFO: pip is still looking at multiple versions of openxlab to determine which version is compatible with other requirements. This could take a while.
INFO: This is taking longer than usual. You might need to provide the dependency resolver with stricter constraints to reduce runtime. See https://pip.pypa.io/warnings/backtracking for guidance. If you want to abort this run, press Ctrl + C.
   ━━━━━━━━━━━━━━━

In [3]:
import pandas as pd
from autogluon.tabular import TabularPredictor
from sklearn.model_selection import train_test_split

# -------------------------------
# 📥 Load & Clean Dataset
# -------------------------------
df = pd.read_csv('WA_Fn-UseC_-Telco-Customer-Churn.csv')

# Drop customer ID (not useful)
df.drop('customerID', axis=1, inplace=True)

# Replace ' ' in TotalCharges with NaN and convert to float
df['TotalCharges'] = pd.to_numeric(df['TotalCharges'], errors='coerce')

# Fill missing values (optional, AutoGluon can handle it too)
df['TotalCharges'] = df['TotalCharges'].fillna(df['TotalCharges'].median())

# Encode target
df['Churn'] = df['Churn'].map({'Yes': 1, 'No': 0})

df

gender  SeniorCitizen Partner Dependents  tenure PhoneService  \
0     Female              0     Yes         No       1           No   
1       Male              0      No         No      34          Yes   
2       Male              0      No         No       2          Yes   
3       Male              0      No         No      45           No   
4     Female              0      No         No       2          Yes   
...      ...            ...     ...        ...     ...          ...   
7038    Male              0     Yes        Yes      24          Yes   
7039  Female              0     Yes        Yes      72          Yes   
7040  Female              0     Yes        Yes      11           No   
7041    Male              1     Yes         No       4          Yes   
7042    Male              0      No         No      66          Yes   

         MultipleLines InternetService OnlineSecurity OnlineBackup  \
0     No phone service             DSL             No          Yes   
1                   No             DSL            Yes           No   
2                   No             DSL            Yes          Yes   
3     No phone service             DSL            Yes           No   
4                   No     Fiber optic             No           No   
...                ...             ...            ...          ...   
7038               Yes             DSL            Yes           No   
7039               Yes     Fiber optic             No          Yes   
7040  No phone service             DSL            Yes           No   
7041               Yes     Fiber optic             No           No   
7042                No     Fiber optic            Yes           No   

     DeviceProtection TechSupport StreamingTV StreamingMovies        Contract  \
0                  No          No          No              No  Month-to-month   
1                 Yes          No          No              No        One year   
2                  No          No          No              No  Month-to-month   
3                 Yes         Yes          No              No        One year   
4                  No          No          No              No  Month-to-month   
...               ...         ...         ...             ...             ...   
7038              Yes         Yes         Yes             Yes        One year   
7039              Yes          No         Yes             Yes        One year   
7040               No          No          No              No  Month-to-month   
7041               No          No          No              No  Month-to-month   
7042              Yes         Yes         Yes             Yes        Two year   

     PaperlessBilling              PaymentMethod  MonthlyCharges  \
0                 Yes           Electronic check           29.85   
1                  No               Mailed check           56.95   
2                 Yes               Mailed check           53.85   
3                  No  Bank transfer (automatic)           42.30   
4                 Yes           Electronic check           70.70   
...               ...                        ...             ...   
7038              Yes               Mailed check           84.80   
7039              Yes    Credit card (automatic)          103.20   
7040              Yes           Electronic check           29.60   
7041              Yes               Mailed check           74.40   
7042              Yes  Bank transfer (automatic)          105.65   

      TotalCharges  Churn  
0            29.85      0  
1          1889.50      0  
2           108.15      1  
3          1840.75      0  
4           151.65      1  
...            ...    ...  
7038       1990.50      0  
7039       7362.90      0  
7040        346.45      0  
7041        306.60      1  
7042       6844.50      0  

[7043 rows x 20 columns]

In [5]:
# -------------------------------
# ✂️ Train-Test Split
# -------------------------------
train_data, test_data = train_test_split(df, test_size=0.2, random_state=42)

# -------------------------------
# 🚀 AutoML Configuration
# -------------------------------
label = 'Churn'

# Custom metric: Balanced Accuracy
predictor = TabularPredictor(
    label=label,
    eval_metric='balanced_accuracy',
    problem_type='binary',
    path='AutoML_Churn_Model'
).fit(
    train_data=train_data,
    time_limit=600,  # 10 minutes max time
    presets='best_quality',  # best ensemble models
    num_bag_folds=5,  # bagging for robustness
    num_stack_levels=2,  # stacking for meta-learning
    hyperparameters={
        'GBM': {},  # LightGBM
        'CAT': {'iterations': 1000},
        'XGB': {'n_estimators': 1000},
        'NN_TORCH': {},
        'RF': {},
        'XT': {},
        'KNN': {},
        # 'custom': ['GBM', 'CAT', 'XGB'],
    }
)

Verbosity: 2 (Standard Logging)
=================== System Info ===================
AutoGluon Version:  1.3.1
Python Version:     3.11.13
Operating System:   Linux
Platform Machine:   x86_64
Platform Version:   #1 SMP PREEMPT_DYNAMIC Sun Mar 30 16:01:29 UTC 2025
CPU Count:          2
Memory Avail:       10.80 GB / 12.67 GB (85.2%)
Disk Space Avail:   65.03 GB / 107.72 GB (60.4%)
Presets specified: ['best_quality']
Setting dynamic_stacking from 'auto' to True. Reason: Enable dynamic_stacking when use_bag_holdout is disabled. (use_bag_holdout=False)
Stack configuration (auto_stack=True): num_stack_levels=2, num_bag_folds=5, num_bag_sets=1
DyStack is enabled (dynamic_stacking=True). AutoGluon will try to determine whether the input data is affected by stacked overfitting and enable or disable stacking as a consequence.
	This is used to identify the optimal `num_stack_levels` value. Copies of AutoGluon will be fit on subsets of the data. Then holdout validation data is used to detect stack

In [6]:
# -------------------------------
# 📊 Leaderboard
# -------------------------------
leaderboard = predictor.leaderboard(test_data, silent=True)
print("\n🏆 Leaderboard:\n", leaderboard)


🏆 Leaderboard:
                   model  score_test  score_val        eval_metric  \
0       CatBoost_BAG_L1    0.782239   0.723947  balanced_accuracy   
1   WeightedEnsemble_L2    0.782239   0.723947  balanced_accuracy   
2   WeightedEnsemble_L4    0.782239   0.723947  balanced_accuracy   
3        XGBoost_BAG_L1    0.776824   0.715792  balanced_accuracy   
4       LightGBM_BAG_L1    0.771355   0.713276  balanced_accuracy   
5       LightGBM_BAG_L3    0.769264   0.717553  balanced_accuracy   
6     ExtraTrees_BAG_L2    0.765241   0.709360  balanced_accuracy   
7   RandomForest_BAG_L3    0.763204   0.704794  balanced_accuracy   
8   RandomForest_BAG_L2    0.762989   0.709843  balanced_accuracy   
9        XGBoost_BAG_L2    0.762402   0.718081  balanced_accuracy   
10      LightGBM_BAG_L2    0.759720   0.716672  balanced_accuracy   
11  RandomForest_BAG_L1    0.759183   0.689281  balanced_accuracy   
12    ExtraTrees_BAG_L1    0.747815   0.684432  balanced_accuracy   
13      CatBoost_

In [8]:
# -------------------------------
# 🔍 Interpretation
# -------------------------------
print("\n🔎 Feature Importance:")
print(predictor.feature_importance(test_data))

Computing feature importance via permutation shuffling for 19 features using 1409 rows with 5 shuffle sets...
	7.3s	= Expected runtime (1.46s per shuffle set)



🔎 Feature Importance:


	2.16s	= Actual runtime (Completed 5 of 5 shuffle sets)


                  importance    stddev   p_value  n  p99_high   p99_low
Contract            0.086775  0.013565  0.000069  5  0.114706  0.058844
tenure              0.051066  0.012635  0.000415  5  0.077081  0.025051
InternetService     0.037190  0.005916  0.000074  5  0.049372  0.025008
OnlineSecurity      0.029790  0.004628  0.000068  5  0.039319  0.020261
TechSupport         0.023603  0.006224  0.000530  5  0.036418  0.010787
MonthlyCharges      0.020215  0.007442  0.001857  5  0.035539  0.004891
PaymentMethod       0.015656  0.001584  0.000012  5  0.018917  0.012396
TotalCharges        0.014284  0.012244  0.029754  5  0.039495 -0.010927
OnlineBackup        0.008793  0.002628  0.000853  5  0.014205  0.003382
MultipleLines       0.008783  0.001496  0.000097  5  0.011863  0.005702
PaperlessBilling    0.007925  0.003112  0.002350  5  0.014333  0.001517
SeniorCitizen       0.005330  0.001212  0.000300  5  0.007825  0.002835
StreamingTV         0.001694  0.002361  0.091913  5  0.006556 -0

In [9]:
# -------------------------------
# 🔮 Prediction & Evaluation
# -------------------------------
preds = predictor.predict(test_data.drop(columns=[label]))
probs = predictor.predict_proba(test_data.drop(columns=[label]))[1]

print("\n📈 Metrics:")
performance = predictor.evaluate(test_data)
print(performance)


📈 Metrics:
{'balanced_accuracy': np.float64(0.782238864678543), 'accuracy': 0.7693399574166075, 'mcc': np.float64(0.5095293371050179), 'roc_auc': np.float64(0.8638685602492573), 'f1': 0.6501614639397201, 'precision': 0.5431654676258992, 'recall': 0.8096514745308311}


In [10]:
# -------------------------------
# 💾 Save & Reload Model
# -------------------------------
predictor.save()  # Save model
loaded_predictor = TabularPredictor.load("AutoML_Churn_Model")

TabularPredictor saved. To load, use: predictor = TabularPredictor.load("/content/AutoML_Churn_Model")
